Задание 1. Решение краевой задачи для ОДУ второго порядка сеточным методом.

In [1]:
from dataclasses import dataclass
from math import exp, sin
from typing import Callable

import numpy as np
import plotly.graph_objs as go
from scipy.sparse import lil_matrix

In [2]:
Function = Callable[[float], float]
Segment = tuple[float, float]
BoundaryCondition = tuple[float, float, float]


@dataclass
class BoundaryValueProblem:
    '''
    Form of the equation:

    ``-p(x)y'' + q(x)y' + r(x)y = f(x)``,
    ``p(x) ≥ p₀ > 0, r(x) ≥ 0 for x ∈ [a, b]``.

    Boundary conditions:
    
    ``α₀y(a) - α₁y'(a) = α, |α₀| + |α₁| ≠ 0, α₀α₁ ≥ 0``,
    
    ``β₀y(b) + β₁y'(b) = β, |β₀| + |β₁| ≠ 0, β₀β₁ ≥ 0``
    '''
    p: Function
    q: Function
    r: Function
    f: Function
    segment: Segment
    left_condition: BoundaryCondition
    right_condition: BoundaryCondition

In [3]:
def solve_tridiagonal_system(matrix: lil_matrix, b: np.ndarray) -> np.ndarray:
    s = np.zeros(b.size)
    t = np.zeros(b.size)
    A, B, C, G = np.insert(matrix.diagonal(-1), 0, 0), -matrix.diagonal(), np.append(matrix.diagonal(1), 0), b

    for i in range(b.size):
        s[i] = C[i] / (B[i] - A[i] * s[i - 1])
        t[i] = (A[i] * t[i - 1] - G[i]) / (B[i] - A[i] * s[i - 1])
    
    y = np.zeros(b.size)
    y[-1] = t[-1]

    for i in reversed(range(b.size - 1)):
        y[i] = s[i] * y[i + 1] + t[i]

    return y


def solve_with_grid(problem: BoundaryValueProblem, N: int) -> tuple[np.ndarray, np.ndarray]:
    size = N + 1
    points, h = np.linspace(*problem.segment, size, retstep=True)

    matrix = lil_matrix((size, size))
    b = np.zeros(size)

    for i in range(1, N):
        x_i = points[i]
        matrix[i, i - 1] = -problem.p(x_i) / (h ** 2) - problem.q(x_i) / (2 * h)
        matrix[i, i] = problem.p(x_i) * 2 / (h ** 2) + problem.r(x_i)
        matrix[i, i + 1] = -problem.p(x_i) / (h ** 2) + problem.q(x_i) / (2 * h)
        b[i] = problem.f(x_i)

    alpha_1, alpha_2, alpha = problem.left_condition
    beta_1, beta_2, beta = problem.right_condition

    matrix[0, :3] = alpha_1 - alpha_2 * ((-3 / 2) / h), -alpha_2 * (2 / h), -alpha_2 * ((-1 / 2) / h)
    b[0] = alpha

    matrix[N, N - 2:] = beta_2 * ((1 / 2) / h), beta_2 * (-2 / h), beta_1 + beta_2 * ((3 / 2) / h)
    b[N] = beta

    coefficient_0, coefficient_N = matrix[0, 2] / matrix[1, 2], matrix[N, N - 2] / matrix[N - 1, N - 2]
    matrix[0] -= coefficient_0 * matrix[1]
    matrix[N] -= coefficient_N * matrix[N - 1]
    b[0] -= coefficient_0 * b[1]
    b[N] -= coefficient_N * b[N - 1]

    return points, solve_tridiagonal_system(matrix, b)


def solve_bvp(problem: BoundaryValueProblem, accuracy: float, start_n: int = 10) -> tuple[np.ndarray, np.ndarray, np.ndarray]:
    n = start_n
    grid_errors = []

    _, previous_solution = solve_with_grid(problem, n)
    while True:
        n *= 2
        points, current_solution = solve_with_grid(problem, n)
        
        errors = np.zeros(current_solution.size)
        for i in range(0, errors.size, 2):
            errors[i] = (current_solution[i] - previous_solution[i // 2]) / 3
        for i in range(1, errors.size - 1, 2):
            errors[i] = (errors[i - 1] + errors[i + 1]) / 2

        error = max(abs(errors))
        grid_errors.append((n, error))

        current_solution += errors
        if error < accuracy:
            break

        previous_solution = current_solution
    return points, current_solution, np.array(grid_errors)

In [4]:
def solution_plot(points: np.ndarray, solution: np.ndarray, exact_solution: Function = None) -> go.Figure:
    fig = go.Figure()
    fig.add_trace(go.Scatter(x=points, y=solution, name='приближенное решение'))

    if exact_solution is not None:
        fig.add_trace(go.Scatter(x=points, y=np.vectorize(exact_solution)(points), name='точное решение'))

    fig.update_layout(title='u(x)')
    fig.update_xaxes(hoverformat='.6f')
    fig.update_yaxes(hoverformat='.6f') 
    return fig


def grid_errors_plot(grid_errors: np.ndarray) -> go.Figure:
    n, errors = zip(*grid_errors)
    fig = go.Figure()
    fig.add_trace(go.Scatter(x=n, y=errors, mode='lines+markers'))
    fig.update_xaxes(title_text='N', type='log', dtick=1, tickformat='.0e')
    fig.update_yaxes(title_text='||Δ||', type='log', tickformat='.0e')
    fig.update_traces(hovertemplate='N = %{x:d}<br>||Δ|| = %{y:.6e}<extra></extra>')
    return fig

In [5]:
u = lambda x: x ** 3 - x ** 2 + x
du = lambda x: 3 * x ** 2 - 2 * x + 1
d2u = lambda x: 6 * x - 2

p = lambda x: 1
q = lambda x: 1
r = lambda x: 1
f = lambda x: -p(x) * d2u(x) + q(x) * du(x) + r(x) * u(x)
a, b = -2, 2

alpha_1, alpha_2 = 1, 1
alpha = alpha_1 * u(a) - alpha_2 * du(a)
beta_1, beta_2 = 1, 2
beta = beta_1 * u(b) + beta_2 * du(b)

l_condition, r_condition = (alpha_1, alpha_2, alpha), (beta_1, beta_2, beta)

problem = BoundaryValueProblem(p, q, r, f, (a, b), l_condition, r_condition)
accuracy = 10 ** -6

points, solution, grid_errors = solve_bvp(problem, accuracy)

solution_plot(points, solution, u).show()
grid_errors_plot(grid_errors).show()

$$-\frac{1}{x - 3}u'' + \left(1 + \frac{x}{2}\right)u' + e^{x/2}u = 2 - x,$$
$$u(-1) = u(1) = 0.$$

In [6]:
p = lambda x: 1 / (x - 3)
q = lambda x: 1 + x / 2
r = lambda x: exp(x / 2)
f = lambda x: 2 - x
segment = (-1, 1)
l_condition, r_condition = (1, 0, 0), (1, 0, 0)

problem = BoundaryValueProblem(p, q, r, f, segment, l_condition, r_condition)
accuracy = 10 ** -6

points, solution, grid_errors = solve_bvp(problem, accuracy)

solution_plot(points, solution).show()
grid_errors_plot(grid_errors).show()

$$u'' - xe^{x}u = \sin(x),$$
$$0.3u(0) - u'(0) = -0.9,$$
$$0.5u(1) + u'(1) = -0.2.$$

In [7]:
p = lambda x: 1
q = lambda x: 0
r = lambda x: x * exp(x)
f = lambda x: -sin(x)
segment = (0, 1)
l_condition, r_condition = (0.3, 1, -0.9), (0.5, 1, -0.2)

problem = BoundaryValueProblem(p, q, r, f, segment, l_condition, r_condition)
accuracy = 10 ** -8

points, solution, grid_errors = solve_bvp(problem, accuracy)

solution_plot(points, solution).show()
grid_errors_plot(grid_errors).show()